In [7]:
import pandas as pd
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import time
import sqlite3
import sqlalchemy
from sqlalchemy import create_engine


**BOT 1**

In [25]:
# login
def login(driver, instahandle, instapassword):
    username = driver.find_element(By.CSS_SELECTOR, "input[name='username']")
    password = driver.find_element(By.CSS_SELECTOR, "input[name='password']")
    username.clear()
    password.clear()
    username.send_keys(instahandle)
    password.send_keys(instapassword)
    driver.find_element(By.CSS_SELECTOR, "button[type='submit']").click()
    time.sleep(5)
    return True

In [26]:
def skip_login_info(driver):
    #save your login info?
    time.sleep(10)
    notnow = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()
def turn_off_notif(driver):
    #turn on notif
    time.sleep(10)
    notnow2 = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()

In [27]:
#searchbox
def search(driver, instapage):
    time.sleep(5)
    searchbox = driver.find_element(By.CSS_SELECTOR, "input[placeholder='Search']")
    searchbox.clear()
    searchbox.send_keys(instapage)
    time.sleep(5)
    #selects the item
    searchbox.send_keys(Keys.ENTER);
    time.sleep(5)
    #clicks enter
    searchbox.send_keys(Keys.ENTER)

In [28]:
def set_window_size(driver):
    time.sleep(5)
    a=driver.get_window_size()
    driver.set_window_size(a["width"], a["height"])

In [29]:
def scroller(driver,timeout):
    #scroll
    time.sleep(5)
    scrolldown = driver.execute_script(
    "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
    match = False
    while not match:
        last_count = scrolldown
        time.sleep(3)
        scrolldown = driver.execute_script(
        "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
        if last_count == scrolldown:
            match = True
        if timeout == 0:
            break
        else:
            timeout-=1


In [30]:
def insta_posts(driver,limit=10):
    posts = []
    links = driver.find_elements(By.TAG_NAME, 'a')
    for link in links:
        post = link.get_attribute('href')
        print(link)
        print(post)
        print(limit)
        if limit==0:
            break;
        if '/p/' in post:
            posts.append(post)
            limit-=1;

    return posts

In [31]:
def getdata(driver,posts, page="",):
    raw_data = []
    for post in posts:
        print(f"Visiting page {post}")
        driver.get(post)
        time.sleep(5)
        shortcode = driver.current_url.split("/")[-2]
        selector = "ul._a9z6"
        try:
            if driver.find_element(By.CSS_SELECTOR, selector) is not None:
                content = driver.find_elements(By.CSS_SELECTOR, selector)
                for con in content:
                    html = con.get_attribute('innerHTML')
                    with open('dummy_sec.html', 'w',encoding="utf-8") as f:
                        f.write(html)
                    soup = BeautifulSoup(html,  'html.parser')

                    for link in soup.find_all('a'):
                        raw_data.append({
                            'tag':link.text,
                            'link':link.attrs.get('href'),
                            'page':soup.find('a').attrs.get('href'),
                            'date':soup.find('time').attrs.get('datetime'),
                            'img':soup.find('img').attrs.get('src')
                        })
                    print(raw_data)
            else:
                print(f"{selector} not found")
        except Exception as e:
            print(e)
        finally:
            time.sleep(5)
    return raw_data


In [32]:
def covert_data_to_df(raw_data):
    df = pd.DataFrame(raw_data)
    new_dataframe=df[df['tag'].str.startswith('#')]
    sorted_df=new_dataframe.drop_duplicates().sort_values('tag')
    return sorted_df

In [34]:
def convert_df_to_csv(df):
    df.to_csv('hastags_rawdata1.csv', index=None)
    print('Process Completed')

**Calling functions**

In [35]:
#installing driver
mdriver = webdriver.Chrome(ChromeDriverManager().install())
mdriver.get("https://www.instagram.com/")
time.sleep(2)
insta_handle='twilightqueenbee1579'
insta_password='!$@%67'
insta_page='random_shotsbyme'
#if login successful
try:
    if login(mdriver,insta_handle,insta_password):
        print("Login successful")
        skip_login_info(mdriver)
        turn_off_notif(mdriver)
        mdriver.get("https://www.instagram.com/explore")
        # set_window_size(mdriver)
        scroller(mdriver,0)
        time.sleep(3)
        fetched_posts=insta_posts(mdriver, 20)
        print(fetched_posts)
        print(f'len of posts {len(fetched_posts)}')
        fetched_data=getdata(mdriver,fetched_posts,insta_page)
        print("The time for fetched data has come...................=^^=")
        print(fetched_data)
        dataframe=covert_data_to_df(fetched_data)
        convert_df_to_csv(dataframe)
        print(dataframe)
    else:
        print("Wrong credentials")
except Exception as e:
     print(e)

# mdriver.quit()



[WDM] - Downloading: 100%|██████████| 6.79M/6.79M [00:00<00:00, 7.63MB/s]
C:\Users\Ananya Misra\AppData\Local\Temp\ipykernel_12616\1411325708.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  mdriver = webdriver.Chrome(ChromeDriverManager().install())


Login successful
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", element="ed5c9dd0-ed85-41c6-b4e8-1b9d9b8f519d")>
https://www.instagram.com/
20
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", element="dd841bfa-b0bd-4e26-954f-c94318eafa68")>
https://www.instagram.com/
20
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", element="44e6ea7c-1463-44b7-bec6-b93dce4d098c")>
https://www.instagram.com/explore/#
20
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", element="e6ee81cc-03f5-4ce6-be9e-b170a9dcd5c0")>
https://www.instagram.com/explore/
20
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", element="088a1398-0389-4a25-b1db-4611c159a029")>
https://www.instagram.com/reels/
20
<selenium.webdriver.remote.webelement.WebElement (session="b30e39d95ed76ae2732a0f3c11d2bbab", e

In [2]:
dataframe

NameError: name 'dataframe' is not defined

**BOT 2**

In [3]:
from datetime import datetime

def save_dataframe(df:pd.DataFrame):
     val = datetime.now().strftime("_%d_%m_%y")
     print(val)
     engine = create_engine('sqlite:///hashtags.sqlite3', echo=False)
     df.to_sql(f'hashtag_{val}', con=engine, if_exists='append')
     return val;

NameError: name 'pd' is not defined

In [1]:
#Adding posts Col to DB

def insertColPost(tableName):
    conn = sqlite3.connect('hashtags.sqlite3')
    cur = conn.cursor()
    doesExists= False
    res=cur.execute(f"""PRAGMA table_info({tableName})""").fetchall()
    for x in range(len(res)):
      if('posts' in res[x]):

          doesExists=True
          break
    if(not doesExists):
        query=f"""ALTER TABLE {tableName} ADD COLUMN posts INTEGER"""
        cur.execute(query);
    conn.commit()
    conn.close()


In [2]:
# going to each hashtag page and extracting the number of posts
def tag_data(driver, row, sleeptime):
    try:
        time.sleep(3)
        prefix = 'https://www.instagram.com/' + row[2]
        driver.get(prefix)
        time.sleep(3)
        no_posts = driver.find_element(By.CLASS_NAME, "_ac2a")
        print(no_posts.text)
        return no_posts.text
    except Exception as e:
            print(e)


In [3]:
def readSqliteTable(tableName,sleeptime):
    sqliteConnection = sqlite3.connect('hashtags.sqlite3')
    cursor = sqliteConnection.cursor()
    print("Connected to SQLite")
    counter=0
    sqlite_select_query = f"""SELECT * from {tableName} ORDER BY tag ASC"""
    cursor.execute(sqlite_select_query)
    records = cursor.fetchall()
    sqliteConnection.close()
    print("Total rows are:  ", len(records))
    print("Printing each row")
    allqueries = ""
    for row in records:

        try:
            val = tag_data(mdriver, row, sleeptime)
            sql_update_query = f"""Update {tableName} set posts = '{val}' where link= '{row[2]}';"""
            allqueries += sql_update_query
            print(sql_update_query)
        except Exception as e:
            print(e)
    conn = sqlite3.connect('hashtags.sqlite3')
    cursor = conn.cursor()
    cursor.executescript(allqueries)
    conn.commit()
    conn.close()
    print("Process Completed")
    mdriver.close()

***Calling Functions***

In [6]:
tableName=save_dataframe(dataframe)
mdriver = webdriver.Chrome(ChromeDriverManager().install())



NameError: name 'save_dataframe' is not defined

In [8]:
tableName='_12_03_23'

mdriver = webdriver.Chrome(ChromeDriverManager().install())
insertColPost("hashtag_"+tableName)
readSqliteTable("hashtag_"+tableName,2)




C:\Users\Ananya Misra\AppData\Local\Temp\ipykernel_9252\3234451958.py:3: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  mdriver = webdriver.Chrome(ChromeDriverManager().install())


Connected to SQLite
Total rows are:   190
Printing each row
72
Update hashtag__12_03_23 set posts = '72' where link= '/explore/tags/viewall50k/';
Message: no such element: Unable to locate element: {"method":"css selector","selector":"._ac2a"}
  (Session info: chrome=111.0.5563.65)
Stacktrace:
Backtrace:
	(No symbol) [0x005EDCE3]
	(No symbol) [0x005839D1]
	(No symbol) [0x00494DA8]
	(No symbol) [0x004C019F]
	(No symbol) [0x004C03AB]
	(No symbol) [0x004EEE62]
	(No symbol) [0x004DAF14]
	(No symbol) [0x004ED57C]
	(No symbol) [0x004DACC6]
	(No symbol) [0x004B6F68]
	(No symbol) [0x004B80CD]
	GetHandleVerifier [0x00863832+2506274]
	GetHandleVerifier [0x00899794+2727300]
	GetHandleVerifier [0x0089E36C+2746716]
	GetHandleVerifier [0x00696690+617600]
	(No symbol) [0x0058C712]
	(No symbol) [0x00591FF8]
	(No symbol) [0x005920DB]
	(No symbol) [0x0059C63B]
	BaseThreadInitThunk [0x76466BD9+25]
	RtlGetFullPathName_UEx [0x778A8FD2+1218]
	RtlGetFullPathName_UEx [0x778A8F9D+1165]

Update hashtag__12_03_2

In [ ]:
# Update hashtag__12_03_23 set posts = 'None' where link= '/explore/tags/pranalirathod/';
# Message: disconnected: not connected to DevTools
#   (failed to check if window was closed: disconnected: not connected to DevTools)
#   (Session info: chrome=111.0.5563.64)
# Stacktrace:
# Backtrace:

In [1]:
dataframe

NameError: name 'dataframe' is not defined

In [4]:
tableName="hashtags__14_03_23"
sqliteConnection = sqlite3.connect('hashtags.sqlite3')
cursor = sqliteConnection.cursor()
print("Connected to SQLite")
counter=0
sqlite_select_query = f"""SELECT * from {tableName} ORDER BY tag ASC"""
cursor.execute(sqlite_select_query)

Connected to SQLite


OperationalError: no such table: hashtags__14_03_23